

# Quick Visualization for Hyperparameter Optimization Analysis

Optuna provides various visualization features in :mod:`optuna.visualization` to analyze optimization results visually.

This tutorial walks you through this module by visualizing the history of lightgbm model for breast cancer dataset.

For visualizing multi-objective optimization (i.e., the usage of :func:`optuna.visualization.plot_pareto_front`),
please refer to the tutorial of `multi_objective`.

<div class="alert alert-info"><h4>Note</h4><p>By using [Optuna Dashboard](https://github.com/optuna/optuna-dashboard), you can also check the optimization history,
   hyperparameter importances, hyperparameter relationships, etc. in graphs and tables.
   Please make your study persistent using `RDB backend <rdb>` and execute following commands to run Optuna Dashboard.

```console
$ pip install optuna-dashboard
$ optuna-dashboard sqlite:///example-study.db
```
   Please check out [the GitHub repository](https://github.com/optuna/optuna-dashboard) for more details.

   .. list-table::
      :header-rows: 1

      * - Manage Studies
        - Visualize with Interactive Graphs
      * - .. image:: https://user-images.githubusercontent.com/5564044/205545958-305f2354-c7cd-4687-be2f-9e46e7401838.gif
        - .. image:: https://user-images.githubusercontent.com/5564044/205545965-278cd7f4-da7d-4e2e-ac31-6d81b106cada.gif</p></div>


In [5]:
import lightgbm as lgb
import numpy as np
import sklearn.datasets
import sklearn.metrics
from sklearn.model_selection import train_test_split
from experiment.exp import Exp_XGBoost
from data.argparser import args_parsing
from data.data_loader import Dataset_XGB
import xgboost as xgb
from sklearn.multioutput import MultiOutputRegressor
from sklearn.metrics import mean_absolute_error
from utils.postprocessing import ProcessedResult
import optuna
from utils.metrics import LinEx, LinLin, weighted_RMSE, RMSE
from data.argparser import args_parsing

# You can use Matplotlib instead of Plotly for visualization by simply replacing `optuna.visualization` with
# `optuna.visualization.matplotlib` in the following examples.
from optuna.visualization import plot_contour
from optuna.visualization import plot_edf
from optuna.visualization import plot_intermediate_values
from optuna.visualization import plot_optimization_history
from optuna.visualization import plot_parallel_coordinate
from optuna.visualization import plot_param_importances
from optuna.visualization import plot_slice

import os

SEED = 42

np.random.seed(SEED)

In [41]:
args = args_parsing()

Args in experiment:
Namespace(data='SRL_NEG_00_04', model='xgboost', loss='rmse', w_rmse_weight=5, linex_weight=0.05, linlin_weight=0.1, input_len=30, target_len=1, timestamp='11-07-2023_09-49-25', root_path='data\\processed\\SRL', data_path='SRL_NEG_00_04.csv', features='S', cols=None, scale='standard', target='capacity_price', freq='d', n_estimators=100, max_depth=3, min_child_weight=1.0, learning_rate=0.1, subsample=1.0, colsample_bytree=1.0, reg_gamma=0.0, reg_alpha=0.0, tune_num_samples=5)



In [42]:
# Loopthrough data and losses to tune XGBoost

import os 
import itertools

datas = [x.split('.')[0] for x in os.listdir("./data/processed/SRL") if x.endswith('csv')]
losses = ['rmse', 'linex', 'linlin', 'w_rmse']


In [47]:
# optuna.logging.get_logger("optuna").addHandler(logging.StreamHandler(sys.stdout))
study_name = f"tune_xgboost_{args.data}_{args.loss}"  # Unique identifier of the study
storage_name = "sqlite:///{}.db".format(study_name)
study = optuna.create_study(study_name=study_name, storage=storage_name,
                            directions=['minimize', 'maximize'],
                            sampler=optuna.samplers.TPESampler(seed=1993),
                            )

study.optimize(xgboost_optuna_objective, n_trials=300, timeout=600)

[I 2023-07-11 22:16:53,046] A new study created in RDB with name: tune_xgboost_SRL_POS_20_24_w_rmse
[I 2023-07-11 22:16:55,067] Trial 0 finished with values: [258304.58, 0.0] and parameters: {'colsample_bytree': 0.9, 'gamma': 0.1, 'learning_rate': 0.19911172069433908, 'max_depth': 12, 'min_child_weight': 3, 'n_estimators': 72, 'reg_alpha': 0.007148985252278011, 'reg_lambda': 8.379291677846228e-05, 'subsample': 0.8, 'w_rmse_weight': 1.9}. 
[I 2023-07-11 22:16:56,581] Trial 1 finished with values: [769433815974.53, 0.0] and parameters: {'colsample_bytree': 0.7, 'gamma': 0.1, 'learning_rate': 0.30896876125681, 'max_depth': 11, 'min_child_weight': 6, 'n_estimators': 106, 'reg_alpha': 0.03839505357046492, 'reg_lambda': 0.3318333089229249, 'subsample': 0.6, 'w_rmse_weight': 9.700000000000001}. 
[I 2023-07-11 22:16:59,071] Trial 2 finished with values: [22846748785053.65, 0.0] and parameters: {'colsample_bytree': 0.6, 'gamma': 0.30000000000000004, 'learning_rate': 0.3624570385356252, 'max_dep

In [44]:
for (data, loss) in list(itertools.product(datas, losses)):
    args.data = data
    args.loss = loss
    # optuna.logging.get_logger("optuna").addHandler(logging.StreamHandler(sys.stdout))
    study_name = f"tune_xgboost_{args.data}_{args.loss}"  # Unique identifier of the study
    storage_name = "sqlite:///{}.db".format(study_name)
    study = optuna.create_study(study_name=study_name, storage=storage_name,
                                directions=['minimize', 'maximize'],
                                sampler=optuna.samplers.TPESampler(seed=1993),
                                )

    study.optimize(xgboost_optuna_objective, n_trials=300, timeout=600)

[I 2023-07-11 09:50:20,077] A new study created in RDB with name: tune_xgboost_SRL_NEG_00_04_rmse
[I 2023-07-11 09:50:21,105] Trial 0 finished with values: [0.15, 1057.4] and parameters: {'colsample_bytree': 0.8, 'gamma': 0.2, 'learning_rate': 0.4689798509435961, 'max_depth': 5, 'min_child_weight': 4, 'n_estimators': 60, 'reg_alpha': 0.04252826173565198, 'reg_lambda': 0.007148985252278011, 'subsample': 0.6}. 
[I 2023-07-11 09:50:22,614] Trial 1 finished with values: [0.15, 1080.6] and parameters: {'colsample_bytree': 0.5, 'gamma': 0.6000000000000001, 'learning_rate': 0.30163419705888395, 'max_depth': 12, 'min_child_weight': 9, 'n_estimators': 68, 'reg_alpha': 0.00034054169412896874, 'reg_lambda': 0.0007675101012546098, 'subsample': 0.8}. 
[I 2023-07-11 09:50:24,052] Trial 2 finished with values: [0.11, 1211.51] and parameters: {'colsample_bytree': 1.0, 'gamma': 0.1, 'learning_rate': 0.28240366207629297, 'max_depth': 12, 'min_child_weight': 6, 'n_estimators': 122, 'reg_alpha': 0.0002399

DuplicatedStudyError: Another study with name 'tune_xgboost_SRL_POS_20_24_w_rmse' already exists. Please specify a different name, or reuse the existing one by setting `load_if_exists` (for Python API) or `--skip-if-exists` flag (for CLI).

Define the objective function.



In [43]:
def xgboost_optuna_objective(trial):
    
    # param = {
    #     "objective": "binary",
    #     "metric": "auc",
    #     "verbosity": -1,
    #     "boosting_type": "gbdt",
    #     "bagging_fraction": trial.suggest_float("bagging_fraction", 0.4, 1.0),
    #     "bagging_freq": trial.suggest_int("bagging_freq", 1, 7),
    #     "min_child_samples": trial.suggest_int("min_child_samples", 5, 100),
    # }
    
    # SEARCH SPACE
    
    match args.loss:
        case 'linex':
            args.linex_weight = trial.suggest_float('linex_weight', 0.001, 1, step=0.01)
        case 'w_rmse':
            args.w_rmse_weight = trial.suggest_float('w_rmse_weight', 1.0, 10.0, step=0.1)
        case 'linlin':
            args.linlin_weight = trial.suggest_float('linlin_weight', 0.05, 0.45, step=0.005)
        
    args.n_estimators = trial.suggest_int("n_estimators", 50, 150)
    args.max_depth = trial.suggest_int("max_depth", 3, 12)
    args.learning_rate = trial.suggest_float("learning_rate", 0.05, 0.5)
    args.min_child_weight = trial.suggest_int('min_child_weight', 1, 10)
    args.gamma = trial.suggest_float('gamma', 0, 1, step=0.1)
    args.subsample = trial.suggest_float('subsample', 0.5, 1.0, step=0.1)
    args.colsample_bytree = trial.suggest_float('colsample_bytree', 0.5, 1.0, step=0.1)
    args.reg_alpha = trial.suggest_loguniform('reg_alpha', 1e-5, 1.0)
    args.reg_lambda = trial.suggest_loguniform('reg_lambda', 1e-5, 1.0)

    exp = Exp_XGBoost(args)
    
    exp.train()
    
    loss, revenue, _ = exp.tune()
    
    # # Add a callback for pruning.
    # pruning_callback = optuna.integration.LightGBMPruningCallback(trial, "auc")
    # gbm = lgb.train(param, dtrain, valid_sets=[dvalid], callbacks=[pruning_callback])

    # preds = gbm.predict(valid_x)
    # pred_labels = np.rint(preds)
    # accuracy = sklearn.metrics.accuracy_score(valid_y, pred_labels)
    return loss, revenue

In [6]:
import logging
import sys

# Add stream handler of stdout to show the messages
optuna.logging.get_logger("optuna").addHandler(logging.StreamHandler(sys.stdout))
study_name = f"tune_xgboost_{args.data}_{args.loss}"  # Unique identifier of the study.
storage_name = "sqlite:///{}.db".format(study_name)
study = optuna.create_study(study_name=study_name, storage=storage_name,
                            directions=['minimize', 'maximize'],
                            sampler=optuna.samplers.TPESampler(seed=11),
                            )

study.optimize(objective, n_trials=300, timeout=600)

[I 2023-07-10 21:02:39,458] A new study created in RDB with name: example-study


A new study created in RDB with name: example-study


[I 2023-07-10 21:02:40,363] Trial 0 finished with values: [86.26, 501.6] and parameters: {'colsample_bytree': 0.7, 'gamma': 0.5, 'learning_rate': 0.37622026813646653, 'linex_weight': 0.181, 'max_depth': 7, 'min_child_weight': 5, 'n_estimators': 51, 'reg_alpha': 0.5117210256953474, 'reg_lambda': 0.17946321632880408, 'subsample': 0.5}. 


Trial 0 finished with values: [86.26, 501.6] and parameters: {'colsample_bytree': 0.7, 'gamma': 0.5, 'learning_rate': 0.37622026813646653, 'linex_weight': 0.181, 'max_depth': 7, 'min_child_weight': 5, 'n_estimators': 51, 'reg_alpha': 0.5117210256953474, 'reg_lambda': 0.17946321632880408, 'subsample': 0.5}. 


[I 2023-07-10 21:02:41,235] Trial 1 finished with values: [48.05, 505.47] and parameters: {'colsample_bytree': 0.5, 'gamma': 0.6000000000000001, 'learning_rate': 0.4357194111827733, 'linex_weight': 0.721, 'max_depth': 11, 'min_child_weight': 2, 'n_estimators': 60, 'reg_alpha': 0.00038180055737136056, 'reg_lambda': 6.159727975507045e-05, 'subsample': 0.5}. 


...

Trial 97 finished with values: [41.77, 665.7] and parameters: {'colsample_bytree': 0.5, 'gamma': 0.8, 'learning_rate': 0.3228983894056431, 'linex_weight': 0.681, 'max_depth': 6, 'min_child_weight': 2, 'n_estimators': 130, 'reg_alpha': 0.8417665272896763, 'reg_lambda': 0.0035363718499627182, 'subsample': 1.0}. 


[I 2023-07-10 21:05:22,494] Trial 98 finished with values: [67.6, 322.23] and parameters: {'colsample_bytree': 0.6, 'gamma': 1.0, 'learning_rate': 0.3996742125099364, 'linex_weight': 0.761, 'max_depth': 8, 'min_child_weight': 8, 'n_estimators': 83, 'reg_alpha': 0.9683768485193817, 'reg_lambda': 0.009991524536906729, 'subsample': 0.5}. 


Trial 98 finished with values: [67.6, 322.23] and parameters: {'colsample_bytree': 0.6, 'gamma': 1.0, 'learning_rate': 0.3996742125099364, 'linex_weight': 0.761, 'max_depth': 8, 'min_child_weight': 8, 'n_estimators': 83, 'reg_alpha': 0.9683768485193817, 'reg_lambda': 0.009991524536906729, 'subsample': 0.5}. 


[I 2023-07-10 21:05:24,410] Trial 99 finished with values: [62.97, 757.23] and parameters: {'colsample_bytree': 0.8, 'gamma': 0.2, 'learning_rate': 0.2732958303366641, 'linex_weight': 0.971, 'max_depth': 4, 'min_child_weight': 10, 'n_estimators': 100, 'reg_alpha': 7.154704796088682e-05, 'reg_lambda': 0.0001624791660873905, 'subsample': 1.0}. 


Trial 99 finished with values: [62.97, 757.23] and parameters: {'colsample_bytree': 0.8, 'gamma': 0.2, 'learning_rate': 0.2732958303366641, 'linex_weight': 0.971, 'max_depth': 4, 'min_child_weight': 10, 'n_estimators': 100, 'reg_alpha': 7.154704796088682e-05, 'reg_lambda': 0.0001624791660873905, 'subsample': 1.0}. 


In [7]:
study = optuna.create_study(study_name=study_name, storage=storage_name, load_if_exists=True)

[I 2023-07-10 21:53:11,327] Using an existing study with name 'example-study' instead of creating a new one.


Using an existing study with name 'example-study' instead of creating a new one.


In [27]:
res = study.trials_dataframe()
study.best_trials
id = res['values_1'].idxmax()
best_params = study.trials[id].params

# Copy configuration of best model

for key in best_params.keys():
    vars(args)[key] = best_params[key]

In [28]:
# Train again using best model

exp = Exp_XGBoost(args)

exp.train()

exp.vali()

# exp.test()

Finished vali!


In [12]:
res

number   values_0  values_1             datetime_start  \
0         0  13.526640   1542.04 2023-07-07 23:21:23.696518   
1         1  15.692992    814.29 2023-07-07 23:21:24.243958   
2         2  24.532835   1397.11 2023-07-07 23:21:24.688490   
3         3  19.411852   1205.86 2023-07-07 23:21:24.977918   
4         4  15.348941   1535.56 2023-07-07 23:21:25.444343   
..      ...        ...       ...                        ...   
195     195  14.423938   1908.91 2023-07-07 23:22:54.912050   
196     196  16.308280   1552.60 2023-07-07 23:22:55.480479   
197     197  17.660408   1568.51 2023-07-07 23:22:55.979927   
198     198  17.465967   1672.04 2023-07-07 23:22:56.625165   
199     199  13.777155   1816.75 2023-07-07 23:22:57.106757   

             datetime_complete               duration  \
0   2023-07-07 23:21:24.243464 0 days 00:00:00.546946   
1   2023-07-07 23:21:24.687492 0 days 00:00:00.443534   
2   2023-07-07 23:21:24.976360 0 days 00:00:00.287870   
3   2023-07-07 23:21:25.443342 0 days 00:00:00.465424   
4   2023-07-07 23:21:25.828173 0 days 00:00:00.383830   
..                         ...                    ...   
195 2023-07-07 23:22:55.479480 0 days 00:00:00.567430   
196 2023-07-07 23:22:55.978918 0 days 00:00:00.498439   
197 2023-07-07 23:22:56.624166 0 days 00:00:00.644239   
198 2023-07-07 23:22:57.104756 0 days 00:00:00.479591   
199 2023-07-07 23:22:57.898750 0 days 00:00:00.791993   

     params_colsample_bytree  params_gamma  params_learning_rate  \
0                        0.8           0.7              0.106270   
1                        1.0           1.0              0.116978   
2                        0.8           0.2              0.285023   
3                        0.7           1.0              0.299828   
4                        0.9           1.0              0.218902   
..                       ...           ...                   ...   
195                      0.9           0.8              0.162617   
196                      0.8           0.2              0.146260   
197                      0.6           0.8              0.318394   
198                      0.8           0.3              0.253315   
199                      0.8           0.7              0.121109   

     params_max_depth  params_min_child_weight  params_n_estimators  \
0                  11                        3                   66   
1                  10                        6                   19   
2                   3                        6                   92   
3                   4                        4                   86   
4                   4                        4                   95   
..                ...                      ...                  ...   
195                 3                        9                   25   
196                 4                        4                   89   
197                12                       10                   27   
198                 5                        5                   61   
199                 5                        8                   68   

     params_reg_alpha  params_reg_lambda  params_subsample     state  
0            0.005590           0.001891               1.0  COMPLETE  
1            0.010866           0.000028               0.8  COMPLETE  
2            0.004769           0.001254               0.7  COMPLETE  
3            0.014491           0.615836               0.6  COMPLETE  
4            0.007613           0.000285               1.0  COMPLETE  
..                ...                ...               ...       ...  
195          0.002750           0.242911               0.9  COMPLETE  
196          0.105533           0.009279               0.9  COMPLETE  
197          0.256103           0.004480               0.9  COMPLETE  
198          0.004232           0.000656               0.9  COMPLETE  
199          0.446780           0.505538               0.8  COMPLETE  

[200 rows x 16 columns]

In [18]:
import plotly.graph_objects as go
import numpy as np
from scipy.interpolate import griddata

# Assuming x, y, z are 1D arrays of data points. Replace these with your actual data.
x = res['params_learning_rate']
y = res['params_max_depth']
z = res['values_1']

# Creating a grid of points where we want to interpolate
grid_x, grid_y = np.mgrid[min(x):max(x):100j, min(y):max(y):100j]

# Performing the 2D interpolation
grid_z = griddata((x, y), z, (grid_x, grid_y), method='cubic')

fig = go.Figure(data =
    go.Contour(
        x=x,
        y=y,
        z=z,
        colorbar={"title": "objective"},
        # colorscale=COLOR_SCALE,
        connectgaps=True,
        contours_coloring="heatmap",
        hoverinfo="none",
        line_smoothing=1.3,
        # reversescale=reverse_scale,
    )
    )

fig.show()


In [ ]:
plot_contour(study, params = ['learning_rate', 'max_depth'], target=lambda t: t.values[1])

## Plot functions
Visualize the optimization history. See :func:`~optuna.visualization.plot_optimization_history` for the details.



In [8]:
optuna.visualization.plot_pareto_front(study, target_names=["loss", "revenue"])

In [6]:
plot_optimization_history(study, target=lambda t: t.values[1])

Visualize the learning curves of the trials. See :func:`~optuna.visualization.plot_intermediate_values` for the details.



In [21]:
plot_intermediate_values(study)

[W 2023-07-07 23:51:29,118] You need to set up the pruning feature to utilize `plot_intermediate_values()`


Visualize high-dimensional parameter relationships. See :func:`~optuna.visualization.plot_parallel_coordinate` for the details.



In [22]:
plot_parallel_coordinate

<function optuna.visualization._parallel_coordinate.plot_parallel_coordinate(study: 'Study', params: 'list[str] | None' = None, *, target: 'Callable[[FrozenTrial], float] | None' = None, target_name: 'str' = 'Objective Value') -> "'go.Figure'">

In [36]:
plot_parallel_coordinate(study, target=lambda t: t.values[0], target_name='Predicted revenue')

[W 2023-07-11 09:46:54,933] Your study does not have any completed trials.


In [15]:
plot_parallel_coordinate(study,  target=lambda t: t.values[1], target_name='Predicted revenue')

Select parameters to visualize.



In [ ]:
plot_parallel_coordinate(study, params=["bagging_freq", "bagging_fraction"])

Visualize hyperparameter relationships. See :func:`~optuna.visualization.plot_contour` for the details.



Select parameters to visualize.



In [ ]:
plot_contour(study, params=["bagging_freq", "bagging_fraction"])

Visualize individual hyperparameters as slice plot. See :func:`~optuna.visualization.plot_slice` for the details.



In [ ]:
plot_slice(study)

Select parameters to visualize.



In [ ]:
plot_slice(study, params=["bagging_freq", "bagging_fraction"])

Visualize parameter importances. See :func:`~optuna.visualization.plot_param_importances` for the details.



In [23]:
plot_param_importances(study, target=lambda t: t.values[0])

Learn which hyperparameters are affecting the trial duration with hyperparameter importance.



In [ ]:
optuna.visualization.plot_param_importances(
    study, target=lambda t: t.duration.total_seconds(), target_name="duration"
)

Visualize empirical distribution function. See :func:`~optuna.visualization.plot_edf` for the details.



In [ ]:
plot_edf(study)

In [9]:
for (data, loss) in list(itertools.product(datas, losses)):
    print(data)

SRL_NEG_00_04
SRL_NEG_00_04
SRL_NEG_00_04
SRL_NEG_00_04
SRL_NEG_04_08
SRL_NEG_04_08
SRL_NEG_04_08
SRL_NEG_04_08
SRL_NEG_08_12
SRL_NEG_08_12
SRL_NEG_08_12
SRL_NEG_08_12
SRL_NEG_12_16
SRL_NEG_12_16
SRL_NEG_12_16
SRL_NEG_12_16
SRL_NEG_16_20
SRL_NEG_16_20
SRL_NEG_16_20
SRL_NEG_16_20
SRL_NEG_20_24
SRL_NEG_20_24
SRL_NEG_20_24
SRL_NEG_20_24
SRL_POS_00_04
SRL_POS_00_04
SRL_POS_00_04
SRL_POS_00_04
SRL_POS_04_08
SRL_POS_04_08
SRL_POS_04_08
SRL_POS_04_08
SRL_POS_08_12
SRL_POS_08_12
SRL_POS_08_12
SRL_POS_08_12
SRL_POS_12_16
SRL_POS_12_16
SRL_POS_12_16
SRL_POS_12_16
SRL_POS_16_20
SRL_POS_16_20
SRL_POS_16_20
SRL_POS_16_20
SRL_POS_20_24
SRL_POS_20_24
SRL_POS_20_24
SRL_POS_20_24


In [12]:
study_name = f"tune_xgboost_{args.data}_{args.loss}"  # Unique identifier of the study.
storage_name = f"sqlite:///optuna_studies/xgboost/{study_name}.db"
study = optuna.create_study(study_name=study_name, storage=storage_name,
                            load_if_exists=True
                            )

[I 2023-07-11 08:48:52,419] Using an existing study with name 'tune_xgboost_SRL_POS_20_24_w_rmse' instead of creating a new one.


Using an existing study with name 'tune_xgboost_SRL_POS_20_24_w_rmse' instead of creating a new one.


In [21]:
study.trials_dataframe()['values_0'].mean()

9.464443204578318e+17

In [ ]:
datas = [x.split('.')[0] for x in os.listdir("./data/processed/SRL") if x.endswith('csv')]
losses = ['rmse', 'linex', 'linlin', 'w_rmse']

In [24]:
datas

['SRL_NEG_00_04',
 'SRL_NEG_04_08',
 'SRL_NEG_08_12',
 'SRL_NEG_12_16',
 'SRL_NEG_16_20',
 'SRL_NEG_20_24',
 'SRL_POS_00_04',
 'SRL_POS_04_08',
 'SRL_POS_08_12',
 'SRL_POS_12_16',
 'SRL_POS_16_20',
 'SRL_POS_20_24']

In [ ]:
for (data, loss) in list(itertools.product(datas, losses)):
    args.data = data
    args.loss = loss
    # optuna.logging.get_logger("optuna").addHandler(logging.StreamHandler(sys.stdout))
    study_name = f"tune_xgboost_{args.data}_{args.loss}"  # Unique identifier of the study
    storage_name = "sqlite:///{}.db".format(study_name)
    study = optuna.create_study(study_name=study_name, storage=storage_name,
                                directions=['minimize', 'maximize'],
                                sampler=optuna.samplers.TPESampler(seed=2312),
                                )

    study.optimize(objective, n_trials=300, timeout=600)

In [60]:
def get_studies(root_path='./optuna_studies/xgboost/',direction=None, time_slot=None, loss=None):
    # assert any(var is not None for var in (loss, time_slot, direction)), 'Need at least loss product name'
    # if loss is not None:
    #     assert loss in ['rmse', 'linex', 'linlin', 'w_rmse'], 'Invalid loss!'
    # if direction is not None:
    #     assert direction in ['NEG', 'POS'], 'Direction is one of [NEG, POS].'
    # if time_slot is not None:   
    #     assert time_slot in ['00_04', '04_08', '08_12', '12_16', '16_20', '20_24'], 'Invalid time slot!'

    
    study_name = f"tune_xgboost_SRL_{direction}_{time_slot}_{loss}"  # Unique identifier of the study
    storage_name = f"sqlite:///{root_path}/{study_name}.db"
    study = optuna.create_study(study_name=study_name, storage=storage_name,
                                load_if_exists=True,
                                )
    return study

In [20]:
class Studies:
    def __init__(self, root_path='./optuna_studies/xgboost/'):
        self.root_path = root_path
        self._load_all_studies()
    
    def _load_all_studies(self):
        study_paths = [path for path in os.listdir() if path.startswith('tune_xgboost_SRL')]
        study_names = [study_path.removeprefix('tune_xgboost_').removesuffix('.db') for study_path in study_paths]
        studies = {}
        studies_df = {}
        for (study_path, study_name) in zip(study_paths, study_names):
            study = self._get_studies(study_name)
            print('LOL')
            
            
        #     studies[study_name] = study
        #     # study.trials_dataframe()
        #     # study.best_trials()
        #     studies_df[study_name] = study.trials_dataframe()
        # self.studies = studies
        # self.studies_df = studies_df
        
    def _get_studies(self, study_name):
    # assert any(var is not None for var in (loss, time_slot, direction)), 'Need at least loss product name'
    # if loss is not None:
    #     assert loss in ['rmse', 'linex', 'linlin', 'w_rmse'], 'Invalid loss!'
    # if direction is not None:
    #     assert direction in ['NEG', 'POS'], 'Direction is one of [NEG, POS].'
    # if time_slot is not None:   
    #     assert time_slot in ['00_04', '04_08', '08_12', '12_16', '16_20', '20_24'], 'Invalid time slot!'

    
        study_name = f"tune_xgboost_SRL_{study_name}"  # Unique identifier of the study
        storage_name = f"sqlite:///{self.root_path}/{study_name}.db"
        study = optuna.create_study(study_name=study_name, storage=storage_name,
                                    load_if_exists=True,
                                    )
        return study

In [21]:
x = Studies(root_path='') 

[I 2023-07-11 23:15:54,922] Using an existing study with name 'tune_xgboost_SRL_SRL_NEG_00_04_linex' instead of creating a new one.
[I 2023-07-11 23:16:01,679] Using an existing study with name 'tune_xgboost_SRL_SRL_NEG_00_04_linlin' instead of creating a new one.


LOL
LOL


[I 2023-07-11 23:16:01,865] Using an existing study with name 'tune_xgboost_SRL_SRL_NEG_00_04_rmse' instead of creating a new one.
[I 2023-07-11 23:16:02,006] Using an existing study with name 'tune_xgboost_SRL_SRL_NEG_00_04_w_rmse' instead of creating a new one.


LOL
LOL


[I 2023-07-11 23:16:02,124] Using an existing study with name 'tune_xgboost_SRL_SRL_NEG_04_08_linex' instead of creating a new one.
[I 2023-07-11 23:16:02,227] Using an existing study with name 'tune_xgboost_SRL_SRL_NEG_04_08_linlin' instead of creating a new one.
[I 2023-07-11 23:16:02,335] Using an existing study with name 'tune_xgboost_SRL_SRL_NEG_04_08_rmse' instead of creating a new one.


...

LOL
LOL


[I 2023-07-11 23:16:08,143] Using an existing study with name 'tune_xgboost_SRL_SRL_SRL_NEG_04_08_linex' instead of creating a new one.
[I 2023-07-11 23:16:08,270] Using an existing study with name 'tune_xgboost_SRL_SRL_SRL_NEG_04_08_linlin' instead of creating a new one.


LOL
LOL


[I 2023-07-11 23:16:08,406] Using an existing study with name 'tune_xgboost_SRL_SRL_SRL_NEG_04_08_rmse' instead of creating a new one.
[I 2023-07-11 23:16:08,520] Using an existing study with name 'tune_xgboost_SRL_SRL_SRL_NEG_04_08_w_rmse' instead of creating a new one.


LOL
LOL


In [86]:
study_path='tune_xgboost_SRL_NEG_00_04_linex.db'
root_path='./'

In [90]:
storage_name = f"sqlite:///{study_path}"
study = optuna.create_study(study_name=study_name, storage=storage_name,
                    load_if_exists=True,
                )

[I 2023-07-11 22:46:57,302] Using an existing study with name 'tune_xgboost_SRL_POS_20_24_w_rmse' instead of creating a new one.


In [100]:
study_paths = [path for path in os.listdir() if path.startswith('tune_xgboost_SRL')]
study_names = [study_path.removeprefix('tune_xgboost_').removesuffix('.db') for study_path in study_paths]
studies = {}
studies_df = {}

In [102]:
for study_path, study_name in zip(study_paths, study_names):
    storage_name = f"sqlite:///{study_path}"
    study = optuna.create_study(study_name=study_name, storage=storage_name,
                        load_if_exists=True,
                        )
    studies[study_name] = study

[I 2023-07-11 22:55:02,824] Using an existing study with name 'SRL_NEG_00_04_linex' instead of creating a new one.
[I 2023-07-11 22:55:02,942] Using an existing study with name 'SRL_NEG_00_04_linlin' instead of creating a new one.
[I 2023-07-11 22:55:03,084] Using an existing study with name 'SRL_NEG_00_04_rmse' instead of creating a new one.
[I 2023-07-11 22:55:03,201] Using an existing study with name 'SRL_NEG_00_04_w_rmse' instead of creating a new one.
[I 2023-07-11 22:55:03,308] Using an existing study with name 'SRL_NEG_04_08_linex' instead of creating a new one.
[I 2023-07-11 22:55:03,424] Using an existing study with name 'SRL_NEG_04_08_linlin' instead of creating a new one.
[I 2023-07-11 22:55:03,528] Using an existing study with name 'SRL_NEG_04_08_rmse' instead of creating a new one.
[I 2023-07-11 22:55:03,661] Using an existing study with name 'SRL_NEG_04_08_w_rmse' instead of creating a new one.
[I 2023-07-11 22:55:03,777] Using an existing study with name 'SRL_NEG_08_12_l

In [106]:
studies['SRL_NEG_00_04_rmse'].best_trials

[]

In [97]:
xgb_studies = Studies(root_path="./")

[I 2023-07-11 22:49:53,092] Using an existing study with name 'SRL_NEG_00_04_linex' instead of creating a new one.
[I 2023-07-11 22:50:46,787] Using an existing study with name 'SRL_NEG_00_04_linlin' instead of creating a new one.
[I 2023-07-11 22:50:52,067] Using an existing study with name 'SRL_NEG_00_04_rmse' instead of creating a new one.
[I 2023-07-11 22:50:53,842] Using an existing study with name 'SRL_NEG_00_04_w_rmse' instead of creating a new one.
[I 2023-07-11 22:51:17,419] Using an existing study with name 'SRL_NEG_04_08_linex' instead of creating a new one.
[I 2023-07-11 22:51:17,500] Using an existing study with name 'SRL_NEG_04_08_linlin' instead of creating a new one.
[I 2023-07-11 22:51:17,570] Using an existing study with name 'SRL_NEG_04_08_rmse' instead of creating a new one.
[I 2023-07-11 22:51:17,630] Using an existing study with name 'SRL_NEG_04_08_w_rmse' instead of creating a new one.
[I 2023-07-11 22:51:17,716] Using an existing study with name 'SRL_NEG_08_12_l

In [76]:
xgb_studies.studies['SRL_POS_00_04_rmse'].trials_dataframe()

Empty DataFrame
Columns: []
Index: []

In [31]:
class Test:
    def __init__(self, root_path='./optuna_studies/xgboost/'):
        self.root_path = root_path
    
    def get_studies(self):
        losses = ['rmse', 'linex', 'linlin', 'w_rmse']
        directions = ['NEG', 'POS']
        time_slots = ['00_04', '04_08', '08_12', '12_16', '16_20', '20_24']
        products = list(itertools.product(directions, time_slots, losses))
        print(products)
        studies = dict()
        for (direction, time_slot, loss) in products:
            study, _ = self.get_study(direction=direction, time_slot=time_slot, loss=loss)
            studies['_'.join([direction, time_slot, loss])] = study
        self.studies = studies
    
    def get_study(self, direction=None, time_slot=None, loss=None):
    # assert any(var is not None for var in (loss, time_slot, direction)), 'Need at least loss product name'
    # if loss is not None:
    #     assert loss in ['rmse', 'linex', 'linlin', 'w_rmse'], 'Invalid loss!'
    # if direction is not None:
    #     assert direction in ['NEG', 'POS'], 'Direction is one of [NEG, POS].'
    # if time_slot is not None:   
    #     assert time_slot in ['00_04', '04_08', '08_12', '12_16', '16_20', '20_24'], 'Invalid time slot!'
    
        study_name = f"tune_xgboost_SRL_{direction}_{time_slot}_{loss}"  # Unique identifier of the study
        storage_name = f"sqlite:///{self.root_path}/{study_name}.db"
        study = optuna.create_study(study_name=study_name, storage=storage_name,
                                    load_if_exists=True,
                                    )
        return study, study_name

In [32]:
t = Test()
x = t.get_studies()

[('NEG', '00_04', 'rmse'), ('NEG', '00_04', 'linex'), ('NEG', '00_04', 'linlin'), ('NEG', '00_04', 'w_rmse'), ('NEG', '04_08', 'rmse'), ('NEG', '04_08', 'linex'), ('NEG', '04_08', 'linlin'), ('NEG', '04_08', 'w_rmse'), ('NEG', '08_12', 'rmse'), ('NEG', '08_12', 'linex'), ('NEG', '08_12', 'linlin'), ('NEG', '08_12', 'w_rmse'), ('NEG', '12_16', 'rmse'), ('NEG', '12_16', 'linex'), ('NEG', '12_16', 'linlin'), ('NEG', '12_16', 'w_rmse'), ('NEG', '16_20', 'rmse'), ('NEG', '16_20', 'linex'), ('NEG', '16_20', 'linlin'), ('NEG', '16_20', 'w_rmse'), ('NEG', '20_24', 'rmse'), ('NEG', '20_24', 'linex'), ('NEG', '20_24', 'linlin'), ('NEG', '20_24', 'w_rmse'), ('POS', '00_04', 'rmse'), ('POS', '00_04', 'linex'), ('POS', '00_04', 'linlin'), ('POS', '00_04', 'w_rmse'), ('POS', '04_08', 'rmse'), ('POS', '04_08', 'linex'), ('POS', '04_08', 'linlin'), ('POS', '04_08', 'w_rmse'), ('POS', '08_12', 'rmse'), ('POS', '08_12', 'linex'), ('POS', '08_12', 'linlin'), ('POS', '08_12', 'w_rmse'), ('POS', '12_16', '

NameError: name 'root_path' is not defined

In [12]:
x.best_trials

[FrozenTrial(number=31, state=TrialState.COMPLETE, values=[0.08, 1804.69], datetime_start=datetime.datetime(2023, 7, 11, 9, 57, 34, 189927), datetime_complete=datetime.datetime(2023, 7, 11, 9, 57, 35, 885581), params={'colsample_bytree': 0.7, 'gamma': 0.0, 'learning_rate': 0.1295068267580946, 'linex_weight': 0.6910000000000001, 'max_depth': 8, 'min_child_weight': 7, 'n_estimators': 127, 'reg_alpha': 0.35381689308943487, 'reg_lambda': 0.003067370895901256, 'subsample': 0.7}, user_attrs={}, system_attrs={}, intermediate_values={}, distributions={'colsample_bytree': FloatDistribution(high=1.0, log=False, low=0.5, step=0.1), 'gamma': FloatDistribution(high=1.0, log=False, low=0.0, step=0.1), 'learning_rate': FloatDistribution(high=0.5, log=False, low=0.05, step=None), 'linex_weight': FloatDistribution(high=0.991, log=False, low=0.001, step=0.01), 'max_depth': IntDistribution(high=12, log=False, low=3, step=1), 'min_child_weight': IntDistribution(high=10, log=False, low=1, step=1), 'n_estim

In [64]:
x = dict()
x["a"] = s

In [13]:
losses = ['rmse', 'linex', 'linlin', 'w_rmse']
directions = ['NEG', 'POS']
time_slots = ['00_04', '04_08', '08_12', '12_16', '16_20', '20_24']

In [18]:
import itertools
product_names = ['_'.join(x) for x in list(itertools.product(directions, time_slots, losses))]

In [25]:
l = list(itertools.product(directions, time_slots, losses))
for (direction, time_slot, loss) in l:
    print(direction)

NEG
NEG
NEG
NEG
NEG
NEG
NEG
NEG
NEG
NEG
NEG
NEG
NEG
NEG
NEG
NEG
NEG
NEG
NEG
NEG
NEG
NEG
NEG
NEG
POS
POS
POS
POS
POS
POS
POS
POS
POS
POS
POS
POS
POS
POS
POS
POS
POS
POS
POS
POS
POS
POS
POS
POS
